In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs

# generate a simple quantum circuit on two qubits
qubits = qcs.Qudits(range(2))

circuit = qcs.Program()
circuit.add_gate(qcs.GATES.h, qubits[0])
circuit.add_gate(qcs.GATES.cx, (qubits[0], qubits[1]))

# add a measurement on both qubits with reset
circuit.add_measurement(qubits, reset=True)

circuit.draw()

In [3]:
# print the program layer that contains the conditional operation:
circuit[-1].operations

{Qudits(labels=[0, 1], name=qudits, dim=2): [ConditionalOperation(operations=[Gate(matrix=[[(1+0j), 0j], [0j, (1+0j)]], name=ID), Gate(matrix=[[0j, (1+0j)], [(1+0j), 0j]], name=X)], register=Register(name=qudits_results, num_bits=2, dim=2))]}

In [4]:
circuit = qcs.Program()
circuit.add_gate(qcs.GATES.h, qubits[0])
circuit.add_gate(qcs.GATES.cx, (qubits[0], qubits[1]))

# add a measurement on both qubits with a reset operation
# if the state is 0, play the identity
# if the state is 1, play a Y gate
circuit.add_measurement(qubits, reset=[qcs.GATES.id, qcs.GATES.y])

circuit.draw()

In [5]:
circuit = qcs.Program()

# add a reset operation at the start of the program and repeat it three times
circuit.add_measurement(qubits[0], reset=True, repeat_reset=3)
circuit.draw()

In [6]:
# define a classifier with a register
register = qcs.Register(name="results", num_outcomes=1)
classifier = qcs.Classifier([0, 0.1], register)

# define two channels for the readout waveform and acquisiton
awg = qcs.Channels(0, "awg")
dig = qcs.Channels(0, "dig")

# define the readout pulse and the integration filter
frequency = 5e9
readout_pulse = qcs.RFWaveform(30e-9, qcs.GaussianEnvelope(), 1, frequency)
integration_filter = qcs.RFWaveform(30e-9, qcs.ConstantEnvelope(), 1, 0)

program = qcs.Program()

program.add_waveform(readout_pulse, awg)
program.add_acquisition(integration_filter, dig, classifier)
program.draw()

In [7]:
# first, define two waveforms to be played for either outcome (0 or 1)
waveform_0 = qcs.RFWaveform(30e-9, qcs.GaussianEnvelope(), 1, frequency)
waveform_1 = qcs.RFWaveform(30e-9, qcs.GaussianEnvelope(), 0.5, frequency)

# add the conditional operation using those waveforms and targeting the awg
# channel
program.add_conditional_operation(
    operations=[waveform_0, waveform_1], target=awg, register=classifier.register
)

program.draw()